
This notebook contains the steps that have been taken to convert the Land use simulation model for the Roman period into land use for 1500.
De Kleijn, M., Beijaard, F., Koomen, E., Van Lanen, R., (2018) Simulating past land use: a modelling framework integrating natural and cultural factors, Journal of Archaeological Science Reports. http://dx.doi.org/10.1016/j.jasrep.2018.04.006 

# Step 1 Updating the claim regions:

From Holland_pop_20241016.gpkg, obtained from Rombert Stapel, a selection was made only for 14_1500. It is not very likely that you every polygon with demographic data produced food for themselves. Therefore a subset with settlement cores have been created. For this we first calculated the number of inhabitants per sqaure meter after which settlement cores were determined by determening a settlement as yes when it is more than 0.003 inhabitans per square meter (which would be 333 m2 per inhabitant , can be modified, this is just an assumption).

In [161]:
import pandas as pd
import geopandas as gpd

In [162]:
demo_hol = gpd.read_file("E:\Dropbox\PROJECTS\IISG_PLUS\Input_IISG\Holland_pop_20241016.gpkg")

In [163]:
demo_hol.head()

NAME NAME_EXT NAME_DISAMB                NAME_ALT SHORT_ID  \
0         Merwede     None        None                    None   HO2240   
1   Hillegersberg     None        None                    None  HO1290A   
2        Rotteban     None        None  Ommoorden en Bospolder  HO1290C   
3  Tutelijnswaard     None        None                    None  HO2255C   
4   Bergschenhoek     None        None                    None  HO1290B   

  PARISH_ID  URBAN ADM0 ADM1          ADM2  ... 17_1821 17_1827 17_1829  \
0    HO2310      0  HRR   HO  Zuid-Holland  ...    80.0    85.0    87.0   
1   HO1290A      0  HRR   HO     Schieland  ...  1399.0  1567.0  1631.0   
2   HO1290A      0  HRR   HO     Schieland  ...   176.0   197.0   205.0   
3   HO2255A      0  HRR   HO  Zuid-Holland  ...    11.0    12.0    12.0   
4   HO1290A      0  HRR   HO     Schieland  ...   901.0   946.0   963.0   

  17_1839 17_1840 17_1849 17_1855 17_1859 17_1895  \
0    92.0    92.0    92.0    99.0   100.0   128.0   
1  1767.0  1764.0  1799.0  1930.0  1965.0  2490.0   
2   223.0   222.0   227.0   243.0   247.0   314.0   
3    13.0    13.0    14.0    15.0    15.0    19.0   
4   977.0   975.0   986.0  1058.0  1077.0  1365.0   

                                            geometry  
0  MULTIPOLYGON (((4.73002 51.82264, 4.72920 51.8...  
1  MULTIPOLYGON (((4.51414 51.94248, 4.51338 51.9...  
2  MULTIPOLYGON (((4.54772 51.97277, 4.54699 51.9...  
3  MULTIPOLYGON (((4.89652 51.75239, 4.89893 51.7...  
4  MULTIPOLYGON (((4.50125 52.00609, 4.50109 52.0...  

[5 rows x 563 columns]

In [164]:
print(demo_hol.columns.values)


['NAME' 'NAME_EXT' 'NAME_DISAMB' 'NAME_ALT' 'SHORT_ID' 'PARISH_ID' 'URBAN'
 'ADM0' 'ADM1' 'ADM2' 'ADM3' 'ADM4' 'ADM5' 'ADM6' 'ADM7' 'ADM8' 'ADM9'
 'HIGH_JURISD' 'MID_JURISD' 'LOW_JURISD' 'ARCH_DIOC' 'DIOCESE' 'ARCH_DEAN'
 'DEANERY' 'ARCH_DIOC_1561' 'DIOCESE_1561' 'ARCH_DEAN_1561' 'DEANERY_1561'
 'SOURCE' 'REMARKS' 'wikipedia' 'NIS_CODE_1800' 'NIS_CODE_xxxx' 'insee'
 'LuxCom' 'acode_1840' 'CBS_1840' '14_last year' '14_first year' '14_1369'
 '14_1374' '14_1382' '14_1387' '14_1394' '14_1396' '14_1397' '14_1399'
 '14_1401' '14_1406' '14_1413' '14_1415' '14_1416' '14_1418' '14_1422'
 '14_1424' '14_1426' '14_1429' '14_1433' '14_1434' '14_1437' '14_1444'
 '14_1445' '14_1457' '14_1458' '14_1462' '14_1463' '14_1464' '14_1466'
 '14_1467' '14_1468' '14_1469' '14_1470' '14_1472' '14_1473' '14_1474'
 '14_1475' '14_1476' '14_1477' '14_1480' '14_1481' '14_1483' '14_1489'
 '14_1490' '14_1492' '14_1493' '14_1494' '14_1495' '14_1496' '14_1497'
 '14_1498' '14_1499' '14_1500' '14_1501' '14_1504' '14_1506'

In [165]:
# create a sub selction for the demographies of 1500
demo_hol_1500 = demo_hol[['NAME', 'SHORT_ID','14_1500', 'geometry']]

In [166]:
demo_hol_1500.head()

NAME SHORT_ID  14_1500  \
0         Merwede   HO2240      0.0   
1   Hillegersberg  HO1290A    336.0   
2        Rotteban  HO1290C     42.0   
3  Tutelijnswaard  HO2255C      0.0   
4   Bergschenhoek  HO1290B    118.0   

                                            geometry  
0  MULTIPOLYGON (((4.73002 51.82264, 4.72920 51.8...  
1  MULTIPOLYGON (((4.51414 51.94248, 4.51338 51.9...  
2  MULTIPOLYGON (((4.54772 51.97277, 4.54699 51.9...  
3  MULTIPOLYGON (((4.89652 51.75239, 4.89893 51.7...  
4  MULTIPOLYGON (((4.50125 52.00609, 4.50109 52.0...

In [167]:
# create a demography densities 
# In order to calculate the number per metric unit the data needs to be projected we project it to EPSG 28992

demo_hol_1500_rd = demo_hol_1500.to_crs(epsg=28992)

# area in sq meters to m
demo_hol_1500_rd['area_m2'] = demo_hol_1500_rd.geometry.area 

# Calculate inhabitants per square m
demo_hol_1500_rd['pop_sq_m'] = demo_hol_1500_rd['14_1500'] / demo_hol_1500_rd['area_m2']


In [168]:
demo_hol_1500_rd

NAME  SHORT_ID  14_1500  \
0            Merwede    HO2240      0.0   
1      Hillegersberg   HO1290A    336.0   
2           Rotteban   HO1290C     42.0   
3     Tutelijnswaard   HO2255C      0.0   
4      Bergschenhoek   HO1290B    118.0   
...              ...       ...      ...   
1258         Madroel  HO1890C2      NaN   
1259   Grafelijkheid   HO9999F      0.0   
1260   Grafelijkheid   HO9999G      0.0   
1261   Grafelijkheid   HO9999H      0.0   
1262        Zuidwijk   HO0870B      NaN   

                                               geometry       area_m2  \
0     MULTIPOLYGON (((109691.950 426207.514, 109635....  8.562177e+06   
1     MULTIPOLYGON (((94969.137 439696.520, 94917.25...  9.877922e+06   
2     MULTIPOLYGON (((97316.730 443039.655, 97266.48...  9.856683e+06   
3     MULTIPOLYGON (((121118.190 418301.742, 121285....  1.822237e+05   
4     MULTIPOLYGON (((94169.034 446783.877, 94157.92...  1.524564e+07   
...                                                 ...           ...   
1258  MULTIPOLYGON (((85630.469 434286.962, 85623.04...  3.353385e+05   
1259  MULTIPOLYGON (((168600.148 510968.548, 149184....  1.818811e+09   
1260  MULTIPOLYGON (((132674.913 547564.182, 136398....  1.649640e+08   
1261  MULTIPOLYGON (((149184.077 521756.256, 168600....  6.442697e+08   
1262  MULTIPOLYGON (((83023.042 457642.861, 82954.64...  3.598099e+07   

      pop_sq_m  
0     0.000000  
1     0.000034  
2     0.000004  
3     0.000000  
4     0.000008  
...        ...  
1258       NaN  
1259  0.000000  
1260  0.000000  
1261  0.000000  
1262       NaN  

[1263 rows x 6 columns]

In [169]:
demo_hol_1500_rd['settlement_core'] = (demo_hol_1500_rd['pop_sq_m'] > 0.003).astype(int)

In [170]:
demo_hol_1500_rd.explore('settlement_core')

In [171]:
# Now we are merging all polygons that are adject to each other that have a value of 0.003 inhabitant per square meter
# Filter polygons where 'settlement_core' == 1
settlement_core = demo_hol_1500_rd[demo_hol_1500_rd['settlement_core'] == 1].copy()

In [172]:
settlement_core.explore()

In [173]:
# Build spatial index and graph of touching polygons using networkx
import networkx as nx
touches_graph = nx.Graph()

# Add all indexes as nodes
touches_graph.add_nodes_from(settlement_core.index)

In [174]:
# Iterate through pairs using spatial index for efficiency
for idx, geom in settlement_core.geometry.items():
    possible_matches_index = list(sindex.intersection(geom.bounds))
    for pos in possible_matches_index:
        idx2 = settlement_core.index[pos]
        if idx != idx2 and geom.touches(settlement_core.iloc[pos].geometry):
            touches_graph.add_edge(idx, idx2)

In [175]:
from shapely.ops import unary_union
# Identify connected components (groups of touching polygons)
components = list(nx.connected_components(touches_graph))

# Dissolve polygons in each connected group
merged_polys = []
for component in components:
    merged_geom = unary_union(settlement_core.loc[list(component)].geometry)
    merged_polys.append(merged_geom)

# Create a new GeoDataFrame with merged geometries
merged_settlement_cores = gpd.GeoDataFrame(geometry=merged_polys, crs=settlement_core.crs)

In [176]:
# next we are creating center point of each polygon after which vornoi are applied
merged_settlement_cores = merged_settlement_cores.copy()
merged_settlement_cores['geometry'] = merged_settlement_cores.geometry.centroid

In [177]:
merged_settlement_cores.explore()

In [178]:
import geopandas as gpd
from shapely import voronoi_polygons
from shapely.geometry import MultiPoint
multipoint = MultiPoint(merged_settlement_cores.geometry.tolist())

# Generate Thiessen/Voronoi polygons
voronoi = voronoi_polygons(multipoint)

# Convert to a GeoDataFrame
voronoi_gdf = gpd.GeoDataFrame(geometry=list(voronoi.geoms), crs=demo_hol_1500_rd.crs)

In [179]:
voronoi_gdf.head()

geometry
0  POLYGON ((-49086.497 477368.234, 74093.803 447...
1  POLYGON ((-49086.497 452176.465, 81749.663 433...
2  POLYGON ((89841.474 419151.351, 87877.466 4184...
3  POLYGON ((-49086.497 281301.276, -49086.497 28...
4  POLYGON ((-49086.497 519338.896, 86249.646 461...

In [180]:
# Clip to boundary
voronoi_gdf_clip = gpd.clip(voronoi_gdf, demo_hol_1500_rd)


In [181]:
voronoi_gdf_clip['unique_id'] = voronoi_gdf_clip.index
voronoi_gdf_clip['unique_id'] = range(1, len(voronoi_gdf_clip) + 1)

In [182]:
voronoi_gdf_clip.explore()

In [183]:
# we now created the claim regions which we will use as input for the PLUS model These regions need to be stored as shapefile projected as RD_new EPSG 28992

voronoi_gdf_clip = voronoi_gdf_clip.to_crs(epsg=28992)
voronoi_gdf_clip.to_file("claimregions.shp")

In [184]:
# Now we perform a union between the voronoi and administrative borders in order to get an estimate on the number of inhabitants per area
union_gdf = gpd.overlay(voronoi_gdf_clip, demo_hol_1500_rd, how='union')

C:\Users\Maurice de Kleijn\AppData\Local\Temp\ipykernel_2780\2251392457.py:2: UserWarning: `keep_geom_type=True` in overlay resulted in 23 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  union_gdf = gpd.overlay(voronoi_gdf_clip, demo_hol_1500_rd, how='union')


In [185]:
union_gdf.explore()

In [186]:
# Since the union messed up the area_m2 we need to calculate that again
union_gdf['area_m2'] = union_gdf.geometry.area

In [187]:
# Next we want to calculate the number of inhabitants per settlement core region (claim region)
union_gdf

unique_id               NAME   SHORT_ID  14_1500       area_m2  \
0           1.0         Numansdorp    HO2050B      0.0  4.026185e+07   
1           1.0  Groot-Cromstrijen    HO2050A      0.0  8.683760e+06   
2           1.0         Den Bommel    HO1960A      0.0  8.473597e+05   
3           1.0      Ooltgensplaat    HO1960B      NaN  3.208284e+07   
4           1.0              Broek    HO2075B      0.0  9.284579e+06   
...         ...                ...        ...      ...           ...   
1853        NaN     Weesperkarspel    HO3920J     17.0  3.442599e-09   
1854        NaN     Weesperkarspel    HO3920I     29.0  1.093234e-08   
1855        NaN            Alkmaar  HO0120B2A     24.0  1.080102e-09   
1856        NaN      Grafelijkheid    HO9999F      0.0  1.039268e-07   
1857        NaN      Grafelijkheid    HO9999H      0.0  1.365164e-07   

      pop_sq_m  settlement_core  \
0     0.000000              0.0   
1     0.000000              0.0   
2     0.000000              0.0   
3          NaN              0.0   
4     0.000000              0.0   
...        ...              ...   
1853  0.000009              0.0   
1854  0.000008              0.0   
1855  0.000029              0.0   
1856  0.000000              0.0   
1857  0.000000              0.0   

                                               geometry  
0     POLYGON ((92596.484 412394.620, 91499.505 4127...  
1     POLYGON ((89841.474 419151.351, 93373.161 4183...  
2     POLYGON ((76734.859 406866.300, 76243.920 4069...  
3     POLYGON ((86769.757 413876.973, 86455.741 4136...  
4     POLYGON ((100800.689 416543.678, 100796.051 41...  
...                                                 ...  
1853  POLYGON ((133674.776 480328.188, 133335.583 48...  
1854  POLYGON ((133674.776 480328.188, 133674.776 48...  
1855  POLYGON ((108697.259 516528.063, 108697.259 51...  
1856  MULTIPOLYGON (((149076.382 538239.967, 148888....  
1857  MULTIPOLYGON (((158791.559 499215.644, 159174....  

[1858 rows x 8 columns]

In [188]:
union_gdf['demo_1500']=  union_gdf['pop_sq_m'] * union_gdf['area_m2']

In [189]:
total_inhabitants_zone = union_gdf.groupby('unique_id')['demo_1500'].sum().reset_index()

In [190]:
total_inhabitants_zone

unique_id     demo_1500
0         1.0   1264.824281
1         2.0   1936.288204
2         3.0  12658.602402
3         4.0   1343.652892
4         5.0   3573.666808
5         6.0   2867.713528
6         7.0   3522.951491
7         8.0   7187.897461
8         9.0   1296.260934
9        10.0  16102.557837
10       11.0   5158.399021
11       12.0   7942.353332
12       13.0   7408.635308
13       14.0   1180.853617
14       15.0   2883.682818
15       16.0   1793.284926
16       17.0   2124.044551
17       18.0   3088.108171
18       19.0   4035.447415
19       20.0   2046.658189
20       21.0   1695.787959
21       22.0  12268.379585
22       23.0   3530.584771
23       24.0  20129.274343
24       25.0  10960.846253
25       26.0  17830.853896
26       27.0   3269.747336
27       28.0   6870.609539
28       29.0  16708.880388
29       30.0  15936.553791
30       31.0   1208.273666
31       32.0   3797.296765
32       33.0   2982.591072
33       34.0   4801.956675
34       35.0  10942.568340
35       36.0   6381.378903
36       37.0  13743.533529

In [191]:
total_weight_all = total_inhabitants_zone['demo_1500'].sum()
total_weight_all

242475.0

In [192]:
total_weight_all_org = demo_hol_1500_rd['14_1500'].sum()
total_weight_all_org

242475.0

Based on Van Lanen et al. 2018 we calculate the demand for arable farming by multiplying the number of inhabitants with the number of ha per person. 

The land-use types we distinguised are:

arable_farming = 0.7 # we assume large settlements and a little bit more effective methods for this period.
pasture = 0.56 # we assume large settlements and a little bit more effective methods for this period.
meadows = 0.49 # we assume large settlements and a little bit more effective methods for this period.

Van Lanen, R., De Kleijn, M., Gouw-Bouman, M., Pierik, H.J. (2018). Exploring Roman and early-medieval habitation of the Rhine-Meuse delta: modelling large-scale demographic changes and corresponding land-use impact. Netherlands Journal of Geosciences, Volume 97, Issue 1-2 pp. 45-6. https://doi.org/10.1017/njg.2018.3 

In [193]:
total_inhabitants_zone['demand_arable_farming']= total_inhabitants_zone['demo_1500']*0.7
total_inhabitants_zone['demand_pasture']= total_inhabitants_zone['demo_1500']*0.56
total_inhabitants_zone['demand_meadows']= total_inhabitants_zone['demo_1500']*0.49

In [194]:
total_inhabitants_zone['RstIntPer'] = total_inhabitants_zone['unique_id']

In [195]:
# Create demand files as configuration for PLUS model
import os
output_folder = "scenario_claims"  # Your existing folder

# Arable Farming = which is named Agriculture

demand_arable_farming = total_inhabitants_zone[['RstIntPer','demand_arable_farming']] 
demand_arable_farming['A1'] = demand_arable_farming ['demand_arable_farming']
demand_arable_farming = demand_arable_farming.drop('demand_arable_farming', axis=1)
demand_arable_farming[['A2', 'B1', 'B2']] = 0 # these are just there since the model is originally a modification of a PBL model with different socio economic scenarios, we should remove this in the future

output_path = os.path.join(output_folder, "Agriculture_rstintper.csv")

demand_arable_farming.to_csv(output_path, sep=';', index=False)

C:\Users\Maurice de Kleijn\AppData\Local\Temp\ipykernel_2780\3107483894.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  demand_arable_farming['A1'] = demand_arable_farming ['demand_arable_farming']


In [196]:
# pasture = which is named grassland
demand_pasture = total_inhabitants_zone[['RstIntPer','demand_pasture']] 
demand_pasture['A1'] = demand_pasture ['demand_pasture']
demand_pasture = demand_pasture.drop('demand_pasture', axis=1)
demand_pasture[['A2', 'B1', 'B2']] = 0 # these are just there since the model is originally a modification of a PBL model with different socio economic scenarios, we should remove this in the future


output_path = os.path.join(output_folder, "grassland_rstintper.csv")
demand_pasture.to_csv(output_path, sep=';', index=False)


C:\Users\Maurice de Kleijn\AppData\Local\Temp\ipykernel_2780\3049236015.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  demand_pasture['A1'] = demand_pasture ['demand_pasture']


In [197]:
# meadows = which is named hay_land
demand_meadows = total_inhabitants_zone[['RstIntPer','demand_meadows']] 
demand_meadows['A1'] = demand_meadows ['demand_meadows']
demand_meadows = demand_meadows.drop('demand_meadows', axis=1)
demand_meadows[['A2', 'B1', 'B2']] = 0 # these are just there since the model is originally a modification of a PBL model with different socio economic scenarios, we should remove this in the future


output_path = os.path.join(output_folder, "hay_land_rstintper.csv")
demand_meadows.to_csv(output_path, sep=';', index=False)

C:\Users\Maurice de Kleijn\AppData\Local\Temp\ipykernel_2780\2967569576.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  demand_meadows['A1'] = demand_meadows ['demand_meadows']


In [198]:
# Since the model also uses some other demands (which we are not using) we also create some empty demand files
empty_claim_list = ["military", "Residential", "unused_land", "woodland"]
demand = {}

for claim in empty_claim_list:
    # Create a new DataFrame with the relevant column
    var = total_inhabitants_zone[['RstIntPer']].copy()

    # Add the extra columns, initialized to 0
    var[['A1', 'A2', 'B1', 'B2']] = 0

    # Save to dictionary
    demand[claim] = var

    # Export to CSV
    output_path = os.path.join(output_folder, f"{claim}_rstintper.csv")
    var.to_csv(output_path, sep=';', index=False)